In [57]:
# Libs
import json
import pandas as pd
import plotly.io as pio
import plotly.express as px

BCN_COORDINATES = {"lat": 41.3851, "lon": 2.1734}  # Center on Barcelona

In [58]:
# Load masterdata and facts
with open("../../data/input/md_aeb.geojson", "r") as f:
    bcn_md_neighborhood = json.load(f)

with open("../../data/input/md_district.geojson", "r") as f:
    bcn_md_district = json.load(f)

df_population = pd.read_csv(
    "../../data/input/ds_population_by_district_neighborhood.csv"
)
df_population_district = (
    df_population.groupby(["district_id", "district_desc"])["population"]
    .sum()
    .sort_values(ascending=False)
    .reset_index(name="population")
)

def generate_map_as_html(fig, file_name):
    html_representation = pio.to_html(fig, full_html=False)
    with open(f'../../data/output/{file_name}.html', 'w') as f:
        f.write(html_representation)

In [59]:
# Total population
total_population = f'Total population in Barcelona (2023): {df_population['population'].sum():,.0f}\n'
# Population by district
population_by_district = f'Overview: \n\n{df_population_district.assign(
    population = df_population_district['population'].apply(lambda x: f"{x:,.0f}")
)[['district_desc', 'population']].to_string(index=False)}'

## Population Overview

In [60]:
print(total_population)

Total population in Barcelona (2023): 1,653,381



## Population by District

In [61]:
print(population_by_district)

Overview: 

      district_desc population
           Eixample    267,841
         Sant Martí    241,888
     Sants-Montjuïc    185,377
     Horta-Guinardó    174,889
         Nou Barris    173,443
        Sant Andreu    151,319
Sarrià-Sant Gervasi    149,096
             Gràcia    122,300
       Ciutat Vella    105,481
          Les Corts     81,747


In [62]:
# Population by district
fig = px.choropleth_mapbox(
    df_population_district,
    geojson=bcn_md_district,
    locations="district_id",
    color="population",
    color_continuous_scale="Greens",
    range_color=(0, 280000),  # max is 17.2K
    mapbox_style="carto-positron",
    zoom=10.4,  # city-level view
    center=BCN_COORDINATES,
    opacity=0.5,
    labels={"id": "ditrict_desc", "population": "population"},
    hover_data={"district_desc": True, "population": ":,"},
)
fig.update_layout(margin={"r": 0, "t": 0, "l": 0, "b": 0})
fig.show()

In [63]:
# generate_map_as_html(fig, 'population_by_district')

## Population by Neightborhood

In [64]:
# Population by neightborhood
fig = px.choropleth_mapbox(
    df_population,
    geojson=bcn_md_neighborhood,
    locations="aeb_id",
    color="population",
    color_continuous_scale="Greens",
    range_color=(0, 18000),  # max is 17.2K
    mapbox_style="carto-positron",
    zoom=10.4,  # city-level view
    center=BCN_COORDINATES,
    opacity=0.5,
    labels={"id": "AEB", "population": "population"},
    hover_data={"neighborhood_desc": True, "population": ":,"},
)
fig.update_layout(margin={"r": 0, "t": 0, "l": 0, "b": 0})
fig.show()

In [65]:
# generate_map_as_html(fig, 'population_by_neighborhood')